<a href="https://colab.research.google.com/github/kurtsenol/Text-Classification/blob/main/method_NER.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!python -m spacy download en_core_web_md

✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_md')


In [2]:
!pip3 install pickle5

     |████████████████████████████████| 133kB 5.3MB/s 
  Created wheel for pickle5: filename=pickle5-0.0.11-cp37-cp37m-linux_x86_64.whl size=219254 sha256=397a0f2f494875921a95c087f6f9b8fb8ac03e8e04f60b76fea0c4190f592667
  Stored in directory: /root/.cache/pip/wheels/a6/90/95/f889ca4aa8b0e0c7f21c8470b6f5d6032f0390a3a141a9a3bd
Successfully built pickle5


In [3]:
import os
import numpy as np
import pandas as pd
import pickle5 as pickle
import re
import random

In [4]:
with open("/content/drive/MyDrive/Colab Notebooks/TopicModeling/Methodology/df_all_final.pkl", "rb") as fh:
  df = pickle.load(fh)

In [5]:
df

JO  ...                                        methodology
0     IJCHM  ...  Methodology\nThe design is qualitative and exp...
1     IJCHM  ...  Data\nThere are no official statistics on the ...
2     IJCHM  ...  3. Research method\nWe searched the empirical ...
3     IJCHM  ...  Methods\nParticipants\nEmployees from operatio...
4     IJCHM  ...  Method\nDesign\nParticipants made dining decis...
...     ...  ...                                                ...
3264   JHTR  ...  \nMETHOD\nMeasures\nSignificant discrepant res...
3265   JHTR  ...  \nMETHOD\nSample and Data Collection\nBecause ...
3266   JHTR  ...  \nMETHOD\nData Collection\nManagement from 13 ...
3267   JHTR  ...  \nMETHOD\nSample\nAn experimental design was e...
3268   JHTR  ...  \nMETHOD\nThe 2003 longitudinal study took pla...

[3269 rows x 8 columns]

In [6]:
df.dropna(subset=["methodology"], inplace=True)

In [7]:
df

JO  ...                                        methodology
0     IJCHM  ...  Methodology\nThe design is qualitative and exp...
1     IJCHM  ...  Data\nThere are no official statistics on the ...
2     IJCHM  ...  3. Research method\nWe searched the empirical ...
3     IJCHM  ...  Methods\nParticipants\nEmployees from operatio...
4     IJCHM  ...  Method\nDesign\nParticipants made dining decis...
...     ...  ...                                                ...
3264   JHTR  ...  \nMETHOD\nMeasures\nSignificant discrepant res...
3265   JHTR  ...  \nMETHOD\nSample and Data Collection\nBecause ...
3266   JHTR  ...  \nMETHOD\nData Collection\nManagement from 13 ...
3267   JHTR  ...  \nMETHOD\nSample\nAn experimental design was e...
3268   JHTR  ...  \nMETHOD\nThe 2003 longitudinal study took pla...

[3076 rows x 8 columns]

In [8]:
df.reset_index(drop=True, inplace=True)

In [9]:
df["PY"].fillna(2010, inplace=True)

In [10]:
df["PY"] = df.PY.astype("int")

In [11]:
df.isnull().sum()

JO              0
AU              0
TI              0
PY              0
DI              1
urls           83
filename       84
methodology     0
dtype: int64

In [12]:
df.drop_duplicates(subset="TI")

JO  ...                                        methodology
0     IJCHM  ...  Methodology\nThe design is qualitative and exp...
1     IJCHM  ...  Data\nThere are no official statistics on the ...
2     IJCHM  ...  3. Research method\nWe searched the empirical ...
3     IJCHM  ...  Methods\nParticipants\nEmployees from operatio...
4     IJCHM  ...  Method\nDesign\nParticipants made dining decis...
...     ...  ...                                                ...
3071   JHTR  ...  \nMETHOD\nMeasures\nSignificant discrepant res...
3072   JHTR  ...  \nMETHOD\nSample and Data Collection\nBecause ...
3073   JHTR  ...  \nMETHOD\nData Collection\nManagement from 13 ...
3074   JHTR  ...  \nMETHOD\nSample\nAn experimental design was e...
3075   JHTR  ...  \nMETHOD\nThe 2003 longitudinal study took pla...

[3076 rows x 8 columns]

In [13]:
# spaCy
import spacy
nlp = spacy.load('en_core_web_md')
# nlp = spacy.load('en_core_web_sm')

In [14]:
# nltk
import nltk
nltk.download(['stopwords', 'punkt'])

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [15]:
df_approaches = pd.read_excel("/content/drive/MyDrive/Colab Notebooks/TopicModeling/Methodology/methodological_approaches.xlsx")
df_approaches

Quantitative             Qualitative
0             quantitative             qualitative
1               regression                    case
2                    scale               interview
3                   survey      interview protocol
4            questionnaire            face to face
5                    panel           transcription
6              correlation                verbatim
7           secondary data             observation
8        variance analysis         semi-structured
9          factor analysis              structured
10      construct validity                  coding
11             reliability                   theme
12      common method bias               selective
13                  sample             open coding
14                   model            axial coding
15               deductive               inductive
16      Multivariate model             exploratory
17   Statistical inference           phenomenology
18             Time Series         grounded theory
19       Conjoint analysis             proposition
20    External reliability               bricolage
21  Intercoder reliability          interpretation
22    Internal reliability             Ethnography
23  Split-half reliability           Triangulation
24      Construct validity           Area sampling
25     Convergent validity         Expert sampling
26     Ecological validity     Accidental sampling
27       External validity    Theoretical sampling
28        Generalizability          Quota Sampling
29       Internal validity    Convenience sampling
30         Transferability      Purposive Sampling
31  Simple random sampling       Snowball Sampling
32     Systematic Sampling  Modal instant sampling
33     Stratified Sampling  Heterogeneity sampling
34      Clustered sampling                     NaN
35     Multistage Sampling                     NaN
36                 Nominal                     NaN
37                 Ordinal                     NaN
38                Discrete                     NaN
39              Continuous                     NaN
40  Cross-sectional survey                     NaN
41        Cronbach's alpha                     NaN

In [16]:
quantitative_entity_list = df_approaches.Quantitative.to_list()
qualitative_entity_list = df_approaches.Qualitative.dropna().to_list()

In [17]:
print(len(quantitative_entity_list))
print(len(qualitative_entity_list))

42
34


In [18]:
method_sections_list = df.methodology.tolist()

In [19]:
method_sections_list

['Methodology\nThe design is qualitative and exploratory, centred on understanding social phenomena through triangulation of direct observation, communication and textual analysis (Frey et al., 1999); contextual subjective accuracy is stressed over generality; and interpretative phenomenology attempts to unravel the social phenomena. The initial focus is on a literature search to fill the research gap identified by Roberts and Shea (2017) relating to the potential physical and psychological accommodation needs of a traveller. Aspects of the individual’s journey are deliberated including: travelling through one’s own room; virtual travels from the room via electronic media; the hotel room as a reconstruction of the intimate sphere; the return to, and transformation of, one’s own room; and the accumulation of souvenirs.\nTrickling through the preliminary research, empirical information complements and extends this theoretical, philosophical perspective. The literature pertaining to hotel

In [20]:
len(method_sections_list)

3076

In [21]:
whole_text = " ".join(method_sections_list)

In [22]:
print(nltk.tokenize.sent_tokenize(df.methodology.iloc[0]))

['Methodology\nThe design is qualitative and exploratory, centred on understanding social phenomena through triangulation of direct observation, communication and textual analysis (Frey et al., 1999); contextual subjective accuracy is stressed over generality; and interpretative phenomenology attempts to unravel the social phenomena.', 'The initial focus is on a literature search to fill the research gap identified by Roberts and Shea (2017) relating to the potential physical and psychological accommodation needs of a traveller.', 'Aspects of the individual’s journey are deliberated including: travelling through one’s own room; virtual travels from the room via electronic media; the hotel room as a reconstruction of the intimate sphere; the return to, and transformation of, one’s own room; and the accumulation of souvenirs.', 'Trickling through the preliminary research, empirical information complements and extends this theoretical, philosophical perspective.', 'The literature pertaini

In [23]:
tokenized = nltk.tokenize.sent_tokenize(whole_text)

In [24]:
# part_1 = nltk.tokenize.sent_tokenize(whole_text[:1000000])

In [25]:
# jobs["Location"] = jobs[jobs.Description.notnull()].apply(lambda row: [(m.start(), m.end()) for m in re.finditer(row["Title"], row["Description"], re.I|re.S)], axis=1)

In [26]:
# [[(m.start(), m.end(), entity_list[3]) for m in re.finditer(entity_list[3], part_1[i], re.I|re.S)] for i in range(len(part_1)) if re.search(entity_list[3], part_1[i], re.I|re.S)]

In [27]:
# [(m.start(), m.end(), entity_list[3]) for i in range(len(part_1)) for m in re.finditer(entity_list[3], part_1[i], re.I|re.S)  if re.search(entity_list[3], part_1[i], re.I|re.S)]

In [28]:
# [(part, {'entities':[(m.start(), m.end(), "quantitative")]}) for part in tokenized if re.search(entity_list[3], part, re.I) for m in re.finditer(entity_list[3], part, re.I|re.S) ]

In [29]:
# [(part, {'entities':[(m.start(), m.end(), "quantitative")]}) for part in tokenized for m in re.finditer(entity_list[3], part, re.I|re.S) if re.search(entity_list[3], part, re.I)]

In [30]:
# tokenized_filtered = [part for part in tokenized if re.search(entity_list[3], part, re.I)]

In [31]:
# len(tokenized_filtered)

In [32]:
# tokenized_filtered

In [33]:
# [[(part, {'entities':[(m.start(), m.end(), "quantitative")]}) for m in re.finditer(entity_list[3], part, re.I|re.S)] for part in tokenized_filtered ]

In [121]:
entity_dict={}
def createTrainData(entity_list, tokenizedDoc, entity_type):
  
  train_list=[]
  for entity in entity_list:
    
    tokenized_filtered = [part for part in tokenizedDoc if re.search(entity, part, re.I)]

    if tokenized_filtered:
      
      df_train = pd.DataFrame()
      df_train["Description"] = tokenized_filtered
      
      entity_dict[entity] = len(df_train)
      print(entity + ": " + str(len(df_train)))

      if len(df_train)>50:
        df_train=df_train.sample(50, random_state=21)
      
      df_train["Title"] = entity

      df_train["Location"] = df_train[df_train.Description.notnull()].apply(lambda row: [(m.start(), m.end()) for m in re.finditer(row["Title"], row["Description"], re.I)], axis=1)

      df_train["Location_"] = df_train["Location"].apply(lambda x: [list(a) for a in x])

      df_train["Location_"].apply(lambda x: [a.append(entity_type) for a in x])

      df_train["Location_1"] = df_train["Location_"].apply(lambda x: [tuple(a) for a in x])

      jobs_list = list(df_train.Description)
      location_list = list(df_train.Location_1)

      train_list_element=[]
      for job, location in zip(jobs_list, location_list):
        loc_dict={}
        loc_dict["entities"] = location
        temp_list = [job,loc_dict]
        temp_tuple= tuple(temp_list)
        train_list_element.append(temp_tuple)

      train_list.extend(train_list_element)

  return train_list

In [122]:
quantitative_train_list = createTrainData(quantitative_entity_list, tokenized, "quantitative")

quantitative: 524
regression: 1789
scale: 9396
survey: 7655
questionnaire: 7177
panel: 1107
correlation: 1538
secondary data: 76
variance analysis: 5
factor analysis: 1204
construct validity: 166
reliability: 2349
common method bias: 305
sample: 8057
model: 8010
deductive: 61
Multivariate model: 1
Statistical inference: 11
Time Series: 185
Conjoint analysis: 76
External reliability: 1
Intercoder reliability: 18
Internal reliability: 42
Split-half reliability: 2
Construct validity: 166
Convergent validity: 295
Ecological validity: 7
External validity: 47
Generalizability: 83
Internal validity: 64
Transferability: 37
Simple random sampling: 21
Systematic Sampling: 22
Stratified Sampling: 30
Multistage Sampling: 4
Nominal: 72
Ordinal: 56
Discrete: 69
Continuous: 225
Cross-sectional survey: 22
Cronbach's alpha: 307


In [123]:
len(quantitative_train_list)

1570

In [124]:
qualitative_train_list = createTrainData(qualitative_entity_list, tokenized, "qualitative")

qualitative: 1128
case: 1818
interview: 4227
interview protocol: 43
face to face: 23
transcription: 71
verbatim: 74
observation: 1007
semi-structured: 225
structured: 599
coding: 834
theme: 1028
selective: 73
open coding: 70
axial coding: 44
inductive: 156
exploratory: 694
phenomenology: 18
grounded theory: 89
proposition: 77
interpretation: 372
Ethnography: 21
Triangulation: 106
Expert sampling: 3
Theoretical sampling: 38
Quota Sampling: 51
Convenience sampling: 249
Purposive Sampling: 146
Snowball Sampling: 88


In [125]:
len(qualitative_train_list)

1290

In [126]:
train_list = quantitative_train_list + qualitative_train_list
len(train_list)

2860

In [127]:
entity_dict

{'Conjoint analysis': 76,
 'Construct validity': 166,
 'Continuous': 225,
 'Convenience sampling': 249,
 'Convergent validity': 295,
 "Cronbach's alpha": 307,
 'Cross-sectional survey': 22,
 'Discrete': 69,
 'Ecological validity': 7,
 'Ethnography': 21,
 'Expert sampling': 3,
 'External reliability': 1,
 'External validity': 47,
 'Generalizability': 83,
 'Intercoder reliability': 18,
 'Internal reliability': 42,
 'Internal validity': 64,
 'Multistage Sampling': 4,
 'Multivariate model': 1,
 'Nominal': 72,
 'Ordinal': 56,
 'Purposive Sampling': 146,
 'Quota Sampling': 51,
 'Simple random sampling': 21,
 'Snowball Sampling': 88,
 'Split-half reliability': 2,
 'Statistical inference': 11,
 'Stratified Sampling': 30,
 'Systematic Sampling': 22,
 'Theoretical sampling': 38,
 'Time Series': 185,
 'Transferability': 37,
 'Triangulation': 106,
 'axial coding': 44,
 'case': 1818,
 'coding': 834,
 'common method bias': 305,
 'construct validity': 166,
 'correlation': 1538,
 'deductive': 61,
 'ex

In [128]:
random.shuffle(train_list)

In [129]:
with open('/content/drive/My Drive/Data/method_train_list_1.pickle', 'wb') as file:
     pickle.dump(train_list,file)

In [130]:
with open("/content/drive/My Drive/Data/method_train_list_1.pickle", "rb") as fp:   # Unpickling
  train_data = pickle.load(fp)

In [131]:
train_data

[('Factor loadings that were greater than .6 indicated convergent validity (Bagozzi and Yi, 1988, Clark-Carter, 1997, Cole, 1987).',
  {'entities': [(52, 71, 'quantitative')]}),
 ('Methodology\nThis research adopted a qualitative approach and a semi-structured interview protocol was designed as the data collection method.',
  {'entities': [(79, 97, 'qualitative')]}),
 ("To test the conceptual model and hypotheses, descriptive analysis, confirmatory factor analysis (CFA), and structural equation modeling techniques (SEM) following Anderson and Gerbing's (1988) two-step approach were employed using SPSS 18 and Amos 17.",
  {'entities': [(80, 95, 'quantitative')]}),
 ('Triangulation of the data revealed significant similarity of the responses among the different focus groups as described in depth in the Results section of this paper.',
  {'entities': [(0, 13, 'qualitative')]}),
 ('As shown in Table 1, given that there are high correlations among variables of cultural characteristics, the 

In [132]:
len(train_data)

2860



```
function ClickConnect(){
console.log("Working"); 
document
  .querySelector('#top-toolbar > colab-connect-button')
  .shadowRoot.querySelector('#connect')
  .click() 
}
setInterval(ClickConnect,60000)
```



In [133]:
from spacy.util import minibatch, compounding

nlp = spacy.load("en_core_web_sm")
labels = ['quantitative', 'qualitative']

def train_model(TRAIN_DATA, n_iter=10):

    # create the built-in pipeline components and add them to the pipeline
    # nlp.create_pipe works for built-ins that are registered with spaCy
    if "ner" not in nlp.pipe_names:
        ner = nlp.create_pipe("ner")
        nlp.add_pipe(ner, last=True)

    else:
        ner = nlp.get_pipe("ner")

    # add labels
    for label in labels:
      ner.add_label(label)
    
    optimizer = nlp.resume_training()
    move_names = list(ner.move_names) 

    # List of pipes you want to train
    pipe_exceptions = ["ner", "trf_wordpiecer", "trf_tok2vec"]

    # List of pipes which should remain unaffected in training
    other_pipes = [pipe for pipe in nlp.pipe_names if pipe not in pipe_exceptions]

    # only train NER
    with nlp.disable_pipes(*other_pipes):

      sizes = compounding(1.0, 4.0, 1.001)
      
      for itn in range(n_iter):
        print(f"starting iteration: {itn}")
        random.shuffle(TRAIN_DATA)
      
        # batch up the examples using spaCy's minibatch
        batches = minibatch(TRAIN_DATA, size=sizes)
        
        # dictionary to store losses
        losses = {}
        
        for batch in batches:
          texts, annotations = zip(*batch)

          # Calling update() over the iteration
          nlp.update(texts, annotations, sgd=optimizer, drop=0.35, losses=losses)
        
        print("Losses", losses)     

In [134]:
train_model(train_data, n_iter=10)

starting iteration: 0
Losses {'ner': 54923.97694397649}
starting iteration: 1
Losses {'ner': 52150.91724115051}
starting iteration: 2
Losses {'ner': 51514.919446304906}
starting iteration: 3
Losses {'ner': 50761.27369862044}
starting iteration: 4
Losses {'ner': 51503.671359244036}
starting iteration: 5
Losses {'ner': 51478.589384598745}
starting iteration: 6
Losses {'ner': 51371.4027335546}
starting iteration: 7
Losses {'ner': 50717.22622735839}
starting iteration: 8
Losses {'ner': 51169.75061577337}
starting iteration: 9
Losses {'ner': 50822.505280240206}


In [135]:
nlp.to_disk("/content/drive/My Drive/Data/method_model_3")

In [136]:
nlp_model = spacy.load("/content/drive/My Drive/Data/method_model_3")

In [137]:
text = df.methodology.iloc[0]
text

'Methodology\nThe design is qualitative and exploratory, centred on understanding social phenomena through triangulation of direct observation, communication and textual analysis (Frey et al., 1999); contextual subjective accuracy is stressed over generality; and interpretative phenomenology attempts to unravel the social phenomena. The initial focus is on a literature search to fill the research gap identified by Roberts and Shea (2017) relating to the potential physical and psychological accommodation needs of a traveller. Aspects of the individual’s journey are deliberated including: travelling through one’s own room; virtual travels from the room via electronic media; the hotel room as a reconstruction of the intimate sphere; the return to, and transformation of, one’s own room; and the accumulation of souvenirs.\nTrickling through the preliminary research, empirical information complements and extends this theoretical, philosophical perspective. The literature pertaining to hotel 

In [138]:
doc = nlp_model(text)

In [139]:
for ent in doc.ents:
  print("text: " + ent.text + " | " + "label: " + ent.label_)

text: qualitative | label: qualitative
text: triangulation | label: qualitative
text: observation | label: qualitative
text: phenomenology | label: qualitative
text: triangulation | label: qualitative
text: inductive | label: qualitative


In [140]:
spacy.displacy.render(doc, style="ent", jupyter=True) # display in Jupyter

In [141]:
for entity in quantitative_entity_list:
  if re.search(entity, text, re.I):
    print([(m.start(), m.end(), entity) for m in re.finditer(entity, text, re.I)])

[(1663, 1674, 'reliability'), (1794, 1805, 'reliability'), (1861, 1872, 'reliability')]
[(1497, 1503, 'sample')]
[(2599, 2604, 'model'), (2737, 2742, 'model')]


In [142]:
for entity in qualitative_entity_list:
    if re.search(entity, text, re.I):
      print([(m.start(), m.end(), entity) for m in re.finditer(entity, text, re.I)])

[(26, 37, 'qualitative'), (1691, 1702, 'qualitative'), (1894, 1905, 'qualitative')]
[(3025, 3029, 'case')]
[(129, 140, 'observation')]
[(2230, 2236, 'coding'), (2468, 2474, 'coding')]
[(1057, 1062, 'theme'), (2195, 2200, 'theme'), (2678, 2683, 'theme'), (2692, 2697, 'theme')]
[(2220, 2229, 'inductive')]
[(42, 53, 'exploratory'), (2415, 2426, 'exploratory')]
[(277, 290, 'phenomenology')]
[(105, 118, 'Triangulation'), (2144, 2157, 'Triangulation')]


In [143]:
text = df.methodology.iloc[121]
text

'Method\nMeasures for study variables\nMeasures for variables in this study were adopted from previous studies (Ajzen, 1991; Filieri and Mcleay, 2014; Meng and Choi, 2016; Lee and Tseng, 2015; Wheeler et al., 2005). The validity of the instruments used in our study were demonstrated in previous tourism and marketing studies. Specifically, three items were used for information authenticity. Three items were adopted to evaluate information sensation. Three items were used for star ratings. Three items were used to evaluate customer reviews. Finally, to evaluate involvement in the ELM, three items were adopted from prior studies. As for the constructs within TPB, three items were adopted to measure attitude; three items were used for subjective norms; three items were used to measure perceived behavior control; Finally, three items were used to estimate intention. All items used in our current study were measured by a Likert scale ranging from one to seven points (Table I). The items were

In [144]:
doc = nlp_model(text)

In [145]:
spacy.displacy.render(doc, style="ent", jupyter=True) # display in Jupyter

In [146]:
text="""
RESEARCH METHOD
Data Collection and Sample Description
The data were provided by Außenwirtschaft Österreich,
a branch of the Austrian Chamber of Commerce that
supports export efforts, and consisted of 194 exporting
firms that had completed an online questionnaire; the
respondents were all senior executives (e.g., chief executive
officers, export directors, export department heads)
with direct responsibility for export decisions. We
excluded 21 firms because of poorly completed questionnaires,
resulting in 173 fully usable responses. Of
the responding companies, 80% were independent companies
(either privately owned or public limited companies),
and 12% were part of a global company; the rest
had other corporate structures. Half the companies were
founded in the preceding 20 years, and their export
experience ranged from 1 to 125 years, with a median
of 12 (M = 20, SD = 21) years. On average, the firms
had 191 full-time employees (range from 1 to 7,800).
Almost all (95%) exported to the European Union, 64%
to other European countries, 38% to Asia, 36% to
Africa and/or the Middle East, 29% to North America,
20% to South or Central America, and 19% to Australia
and/or New Zealand. Half the companies
exported to 10 countries or fewer (M = 20, SD = 25),
and the average export dependence (i.e., export-to-total
sales ratio) was 53% (SD = 33%).
To judge the representativeness of our sample, we compared
it with official statistical data on exporting.
According to Statistik Austria, the national statistics
office, 43% of all Austrian exporters sell to a single
country only; however, the volume of exports accounted
for by this group is only 2% (Hodel 2004, 2012). This
group is of little relevance for the current study because
firms with a single export destination are unlikely to
engage in systematic segmentation activities (or to participate
in a study on export segmentation). This is
indeed reflected in the composition of our sample: only
2% of the respondent firms export to a single country
only. The majority of our respondents export to
between 2 and 19 countries (66%) and the rest (32%)
to 20+ countries. The corresponding groups in the
population are 52% and 6% and account for 30% and
68% of all exports, respectively (Hodel 2012). Thus,
our sample seems well representative of the Austrian
companies that are responsible for the bulk of the country’s
export activity and for which export segmentation
is likely to be important, considering the large number
of export markets served.4
Construct Measurement
Table 2 lists the measurements of all constructs in our
model, together with relevant psychometric information.
We measured firm size by the log-transformed number of
employees (Erramilli 1991), export experience by the
years a firm has been exporting (Winklhofer and Diamantopoulos
2002), export dependence as the exportto-
total sales ratio (Diamantopoulos and Inglis 1988;
Katsikeas 1994), export diversity by the number of
countries to which a firm exports (Dhanaraj and
Beamish 2003),5 and export market turbulence according
to Jaworski and Kohli’s (1993) well-established
scale.
For export segmentation commitment, we developed
our own five-item scale, which captured managers’ attitudes
and behavior toward the market segmentation
process. For export segmentation strategy, we itemized
the three strategic options and asked respondents to
specify their agreement with each option. This approach
acknowledges that the fit of the strategy with its context
is critical (Hultman, Robson, and Katsikeas 2009). We
specified segmentation bases as the number of distinct
segmentation variables the firm used (based on a checklist
of 21 criteria for segmenting business-to-consumer
markets and 14 criteria for segmenting business-tobusiness
markets).
For export segmentation effectiveness, we adapted the
basic four-dimensional structure developed by Foedermayr
and colleagues (Foedermayr and Diamantopoulos
2008a; Foedermayr, Diamantopoulos, and Sichtmann
2009), which consisted of targeting performance, positioning
performance, adaptability to change, and cost
reduction.6 Originally, the dimensions were operationalized
with formative indicators; however, the majority of
items under each dimension in the original model seem
to share a common cause, which suggests that reflective
measurement is more appropriate. The psychometric
properties shown in Table 2 strongly support this measurement
respecification.
For strategic export performance and financial export
performance, we adapted items from Zou and Cavusgil
(2002) and Zou, Taylor, and Osland (1998). The indicators
for strategic export performance are export market
share and rate of new market entry, and export financial
performance consists of export sales, export profits, and
export growth. Customer satisfaction comprises three
items about offerings, how consumers are treated, and
how their complaints have been handled. Consistent
with other investigations of export performance (e.g.,
Hooley et al. 2005; Hultman, Robson, and Katsikeas
2009; Morgan, Kaleka, and Katsikeas 2004), we relied
on self-reported measures.

"""

In [147]:
doc = nlp_model(text)

In [148]:
spacy.displacy.render(doc, style="ent", jupyter=True) # display in Jupyter

In [149]:
for entity in quantitative_entity_list:
    if re.search(entity, text, re.I):
      print([(m.start(), m.end(), entity) for m in re.finditer(entity, text, re.I)])

[(3119, 3124, 'scale'), (3193, 3198, 'scale')]
[(251, 264, 'questionnaire'), (483, 496, 'questionnaire')]
[(37, 43, 'sample'), (1399, 1405, 'sample'), (1952, 1958, 'sample'), (2276, 2282, 'sample')]
[(2597, 2602, 'model'), (4258, 4263, 'model')]
